# Konvertering av N50 Vektor til GeoParquet

## 1. Last ned N50 Kartdata

![Geonorge N50](img/geonorge-n50.png)

Vektordata kan fritt lastes ned fra kartkatalogen.geonorge.no, du finner N50 [Her](https://kartkatalog.geonorge.no/metadata/n50-kartdata/ea192681-d039-42ec-b1bc-f3ce04c189ac)

Til denne demoen brukes:
- `Hele landet`
- `UTM 33`
- `FGBD`

![Geonorge Last ned](img/geonorge-lastned.png)

Du får en zip fil når du laster ned, pakk ut denne i `src/geoparquet`. Git er satt opp til å ikke tracke `.gdb` mapper.

In [ ]:
# import packages
import fiona
import geopandas as gpd
from pathlib import Path

import utils

## Data input

Starter med å lese ut alle lagene som finnes i `.gdb` filen.

In [ ]:
# Leser alle lagene fra.gdb filen
path = utils.get_workdir() / Path("Basisdata_0000_Norge_25833_N50Kartdata_FGDB.gdb")
layers = fiona.listlayers(path)
print(layers)

## Parquet produksjon

For hvert lag produseres en parquet fil i `/out` mappen.

In [ ]:
# Oppretter /out mappen
utils.create_dir("out")
# Leser hvert lag fra .gdb filen og skriver til geoparquet
for layer in layers:
    try:
        n50_df = gpd.read_file(path, layer=layer)
        n50_df.to_parquet(
            path=f"out/{layer}.snappy.parquet",
            compression="snappy",
            geometry_encoding="WKB",
            write_covering_bbox=True,
        )
    except Exception as e:
        print(f"Failed to load layer: {layer} with error: {e}")

## Setter fil og bbox

In [35]:
file_path = 'out/N50_Samferdsel_senterlinje.snappy.parquet'
# file_path = 'out/N50_Arealdekke_omrade.snappy.parquet'
xmin = 82100
xmax = 96000
ymin = 6461800
ymax = 6470500

## Initialiserer en DuckDB database i minne

Credit: https://github.com/Norkart/syntaks-2025/blob/main/parquet-create.ipynb

In [ ]:
import duckdb

# Connect to DuckDB
con = duckdb.connect(database=':memory:')

# Load the necessary extensions
con.execute("INSTALL spatial;")
con.execute("LOAD spatial;")

con.execute("INSTALL httpfs;")
con.execute("LOAD httpfs;")



## Leser ut metadata

In [37]:
query = f"""
SELECT *
FROM parquet_metadata('{file_path}')
"""
result = con.query(query).to_df()
result

file_name  row_group_id  \
0   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
1   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
2   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
3   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
4   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
5   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
6   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
7   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
8   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
9   out/N50_Samferdsel_senterlinje.snappy.parquet             0   
10  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
11  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
12  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
13  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
14  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
15  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
16  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
17  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
18  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
19  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
20  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
21  out/N50_Samferdsel_senterlinje.snappy.parquet             0   
22  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
23  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
24  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
25  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
26  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
27  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
28  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
29  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
30  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
31  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
32  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
33  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
34  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
35  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
36  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
37  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
38  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
39  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
40  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
41  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
42  out/N50_Samferdsel_senterlinje.snappy.parquet             1   
43  out/N50_Samferdsel_senterlinje.snappy.parquet             1   

    row_group_num_rows  row_group_num_columns  row_group_bytes  column_id  \
0              1048576                     22        309986742          0   
1              1048576                     22        309986742          1   
2              1048576                     22        309986742          2   
3              1048576                     22        309986742          3   
4              1048576                     22        309986742          4   
5              1048576                     22        309986742          5   
6              1048576                     22        309986742          6   
7              1048576                     22        309986742          7   
8              1048576                     22        309986742          8   
9              1048576                     22        309986742          9   
10             1048576                     22        309986742         10   
11             1048576                     22        309986742         11   
12             1048576 

## Leser schema

In [38]:

query = f"""
SELECT *
FROM parquet_schema('{file_path}')
"""
result = con.query(query).to_df()
result

file_name                   name  \
0   out/N50_Samferdsel_senterlinje.snappy.parquet                 schema   
1   out/N50_Samferdsel_senterlinje.snappy.parquet                objtype   
2   out/N50_Samferdsel_senterlinje.snappy.parquet         datafangstdato   
3   out/N50_Samferdsel_senterlinje.snappy.parquet       oppdateringsdato   
4   out/N50_Samferdsel_senterlinje.snappy.parquet             sporantall   
5   out/N50_Samferdsel_senterlinje.snappy.parquet            anleggstype   
6   out/N50_Samferdsel_senterlinje.snappy.parquet                 medium   
7   out/N50_Samferdsel_senterlinje.snappy.parquet             malemetode   
8   out/N50_Samferdsel_senterlinje.snappy.parquet            noyaktighet   
9   out/N50_Samferdsel_senterlinje.snappy.parquet            rutemerking   
10  out/N50_Samferdsel_senterlinje.snappy.parquet  vedlikeholdsansvarlig   
11  out/N50_Samferdsel_senterlinje.snappy.parquet              vegnummer   
12  out/N50_Samferdsel_senterlinje.snappy.parquet           motorvegtype   
13  out/N50_Samferdsel_senterlinje.snappy.parquet                typeveg   
14  out/N50_Samferdsel_senterlinje.snappy.parquet            vegkategori   
15  out/N50_Samferdsel_senterlinje.snappy.parquet                vegfase   
16  out/N50_Samferdsel_senterlinje.snappy.parquet             banestatus   
17  out/N50_Samferdsel_senterlinje.snappy.parquet           SHAPE_Length   
18  out/N50_Samferdsel_senterlinje.snappy.parquet               geometry   
19  out/N50_Samferdsel_senterlinje.snappy.parquet                   bbox   
20  out/N50_Samferdsel_senterlinje.snappy.parquet                   xmin   
21  out/N50_Samferdsel_senterlinje.snappy.parquet                   ymin   
22  out/N50_Samferdsel_senterlinje.snappy.parquet                   xmax   
23  out/N50_Samferdsel_senterlinje.snappy.parquet                   ymax   

          type type_length repetition_type  num_children converted_type  \
0         None        None        REQUIRED            19           None   
1   BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
2   BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
3   BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
4   BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
5   BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
6   BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
7   BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
8        INT32        None        OPTIONAL          <NA>           None   
9   BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
10  BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
11      DOUBLE        None        OPTIONAL          <NA>           None   
12  BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
13  BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
14  BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
15  BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
16  BYTE_ARRAY        None        OPTIONAL          <NA>           UTF8   
17      DOUBLE        None        OPTIONAL          <NA>           None   
18  BYTE_ARRAY        None        OPTIONAL          <NA>           None   
19        None        None        OPTIONAL             4           None   
20      DOUBLE        None        OPTIONAL          <NA>           None   
21      DOUBLE        None        OPTIONAL          <NA>           None   
22      DOUBLE        None        OPTIONAL          <NA>           None   
23      DOUBLE        None        OPTIONAL          <NA>           None   

    scale  precision  field_id  logical_type  
0    <NA>       <NA>      <NA>          None  
1    <NA>       <NA>      <NA>  StringType()  
2    <NA>       <NA>      <NA>  StringType()  
3    <NA>       <NA>      <NA>  StringType()  
4    <NA>       <NA>      <N

## Leser vektordata

In [39]:

query = f"""
SELECT *
FROM read_parquet('{file_path}')
LIMIT 10
"""
result = con.query(query).to_df()
result

objtype          datafangstdato        oppdateringsdato sporantall  \
0    Bane  1996/07/01 00:00:00+00  2025/01/05 00:00:00+00          F   
1    Bane  1973/01/01 00:00:00+00  2025/01/05 00:00:00+00          E   
2    Bane  1985/01/01 00:00:00+00  2025/01/05 00:00:00+00          E   
3    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
4    Bane  1993/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
5    Bane  1995/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
6    Bane  1999/11/03 00:00:00+00  2025/01/05 00:00:00+00          F   
7    Bane  1979/01/01 00:00:00+00  2025/01/05 00:00:00+00          E   
8    Bane  1988/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
9    Bane  1993/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   

  anleggstype medium malemetode  noyaktighet rutemerking  \
0           F      U        fot         2000        None   
1           J      U        dig         1500        None   
2           J      T        dig         1500        None   
3           J      T        fot         2000        None   
4           J      T        fot         2000        None   
5           J      U        fot         2000        None   
6           F      T        ukj         2500        None   
7           J      U        dig         1500        None   
8           J      T        dig         1500        None   
9           J      T        fot         2000        None   

  vedlikeholdsansvarlig  vegnummer motorvegtype typeveg vegkategori vegfase  \
0                  None        NaN         None    None        None    None   
1                  None        NaN         None    None        None    None   
2                  None        NaN         None    None        None    None   
3                  None        NaN         None    None        None    None   
4                  None        NaN         None    None        None    None   
5                  None        NaN         None    None        None    None   
6                  None        NaN         None    None        None    None   
7                  None        NaN         None    None        None    None   
8                  None        NaN         None    None        None    None   
9                  None        NaN         None    None        None    None   

  banestatus  SHAPE_Length                                           geometry  \
0          I   1943.957349  [4, 4, 0, 0, 0, 0, 0, 0, 228, 133, 126, 72, 83...   
1          I    242.078258  [4, 4, 0, 0, 0, 0, 0, 0, 228, 50, 72, 72, 132,...   
2          I    874.861565  [4, 4, 0, 0, 0, 0, 0, 0, 16, 28, 122, 72, 29, ...   
3          I     19.755126  [4, 4, 0, 0, 0, 0, 0, 0, 129, 127, 167, 71, 14...   
4          I   5862.380461  [4, 4, 0, 0, 0, 0, 0, 0, 168, 115, 164, 72, 89...   
5          I    396.076308  [4, 4, 0, 0, 0, 0, 0, 0, 160, 7, 24, 73, 220, ...   
6          I     51.988818  [4, 4, 0, 0, 0, 0, 0, 0, 176, 66, 130, 72, 189...   
7          I    290.464595  [4, 4, 0, 0, 0, 0, 0, 0, 153, 32, 254, 72, 14,...   
8          I     73.112966  [4, 4, 0, 0, 0, 0, 0, 0, 98, 51, 248, 198, 189...   
9          I    842.951868  [4, 4, 0, 0, 0, 0, 0, 0, 206, 58, 68, 72, 161,...   

                                                bbox  
0  {'xmin': 260631.5700000003, 'ymin': 6649641.9,...  
1  {'xmin': 205003.5700000003, 'ymin': 6700610.22...  
2  {'xmin': 256112.25999999978, 'ymin': 6692622.9...  
3  {'xmin': 85759.00999999978, 'ymin': 6467782.88...  
4  {'xmin': 336797.26999999955, 'ymin': 6693036.8...  
5  {'xmin': 622714.0, 'ymin': 7591150.0, 'xmax': ...  
6  {'xmin': 266773.5099999998, 'ymin': 6642782.52...  
7  {'xmin': 520452.7999999998, 'ymin': 7442567.18...  
8  {'xmin': -31769.69000000041, 'ymin': 6573022.6...  
9  {'xmin': 200939.21999999974, 'ymin': 6880720.8...

## Leser vektor data i bounding box

In [40]:
query = f"""
SELECT *
FROM read_parquet('{file_path}')
WHERE bbox.xmin BETWEEN {xmin} AND {xmax}
AND bbox.ymin BETWEEN {ymin} AND {ymax}
LIMIT 10;
"""
result = con.query(query).to_df()
result

objtype          datafangstdato        oppdateringsdato sporantall  \
0    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
1    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
2    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
3    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
4    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
5    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
6    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
7    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          F   
8    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   
9    Bane  1990/07/01 00:00:00+00  2025/01/05 00:00:00+00          E   

  anleggstype medium malemetode  noyaktighet rutemerking  \
0           J      T        fot         2000        None   
1           J      T        fot         2000        None   
2           J      T        fot         2000        None   
3           J      L        fot         2000        None   
4           J      U        fot         2000        None   
5           J      U        fot         2000        None   
6           J      T        fot         2000        None   
7           J      T        fot         2000        None   
8           J      T        fot         2000        None   
9           J      T        fot         2000        None   

  vedlikeholdsansvarlig  vegnummer motorvegtype typeveg vegkategori vegfase  \
0                  None        NaN         None    None        None    None   
1                  None        NaN         None    None        None    None   
2                  None        NaN         None    None        None    None   
3                  None        NaN         None    None        None    None   
4                  None        NaN         None    None        None    None   
5                  None        NaN         None    None        None    None   
6                  None        NaN         None    None        None    None   
7                  None        NaN         None    None        None    None   
8                  None        NaN         None    None        None    None   
9                  None        NaN         None    None        None    None   

  banestatus  SHAPE_Length                                           geometry  \
0          I     19.755126  [4, 4, 0, 0, 0, 0, 0, 0, 129, 127, 167, 71, 14...   
1          I    134.898729  [4, 4, 0, 0, 0, 0, 0, 0, 88, 103, 167, 71, 176...   
2          I    785.275060  [4, 4, 0, 0, 0, 0, 0, 0, 165, 15, 166, 71, 127...   
3          I     53.825283  [4, 4, 0, 0, 0, 0, 0, 0, 64, 133, 167, 71, 173...   
4          I    136.496584  [4, 4, 0, 0, 0, 0, 0, 0, 128, 79, 165, 71, 204...   
5          I     80.815509  [4, 4, 0, 0, 0, 0, 0, 0, 142, 181, 164, 71, 23...   
6          I    186.820767  [4, 4, 0, 0, 0, 0, 0, 0, 67, 232, 166, 71, 160...   
7          I   1310.565115  [4, 4, 0, 0, 0, 0, 0, 0, 39, 16, 168, 71, 5, 8...   
8          I    266.032136  [4, 4, 0, 0, 0, 0, 0, 0, 70, 218, 164, 71, 242...   
9          I    188.404937  [4, 4, 0, 0, 0, 0, 0, 0, 67, 232, 166, 71, 61,...   

                                                bbox  
0  {'xmin': 85759.00999999978, 'ymin': 6467782.88...  
1  {'xmin': 85710.69000000041, 'ymin': 6467544.48...  
2  {'xmin': 85023.29000000004, 'ymin': 6470079.56...  
3  {'xmin': 85770.5, 'ymin': 6467798.949999999, '...  
4  {'xmin': 84639.0, 'ymin': 6467558.07, 'xmax': ...  
5  {'xmin': 84331.11000000034, 'ymin': 6467700.66...  
6  {'xmin': 85456.53000000026, 'ymin': 6467664.09...  
7  {'xmin': 86048.30999999959, 'ymin': 6466690.64...  
8  {'xmin': 84404.54999999981, 'ymin': 6467577.09...  
9  {'xmin': 85456.53000000026, 'ymin': 6467614.84...

## Viser data på interaktivt kart

In [36]:
kristiansand = gpd.read_parquet(
    path=file_path,
    bbox=(xmin, ymin, xmax, ymax)
)
kristiansand.explore()